$$
\def\CC{\bf C}
\def\QQ{\bf Q}
\def\RR{\bf R}
\def\ZZ{\bf Z}
\def\NN{\bf N}
$$
# Project Euler one-liners

Authors  
-   Thierry Monteil
-   Contributors of projecteuler.net

License  
CC BY-NC-SA 2.0

See <https://projecteuler.net>

> Project Euler is a series of challenging mathematical/computer programming problems that will require more than just mathematical insights to solve. Although mathematics will help you arrive at elegant and efficient methods, the use of a computer and programming skills will be required to solve most problems. The problems range in difficulty and for many the experience is inductive chain learning. That is, by solving one problem it will expose you to a new concept that allows you to undertake a previously inaccessible problem. So the determined participant will slowly but surely work his/her way through every problem.

For each of the first ten Project Euler problems listed below, find a one-line solution with Sage, do not reinvent the wheel !

Note that the proposed answers are not necessarilly optimal, and could be discussed further, actually some variations are copied from the assignments, so thanks for the discoveries ! See also the various comments surrounding some answers. Don't hesitate to use the `%time` and `%timeit` jupyter magic to compare the speed of different solutions (on the older Sage notebook, replace them with `timeit('expression')`). We conclude the worksheet by a summary of some advices we learnt on the way.

## 1: Multiples of 3 and 5

### Question

If we list all the natural numbers below $10$ that are multiples of $3$ or $5$, we get $3$, $5$, $6$ and $9$. The sum of these multiples is $23$.

Find the sum of all the multiples of $3$ or $5$ below $1000$.

### Answer

In [ ]:
sum(i for i in range(1000) if i % 3 == 0 or i % 5 == 0)

233168

## 2: Even Fibonacci numbers

### Question

Each new term in the Fibonacci sequence is generated by adding the previous two terms. By starting with $1$ and $2$, the first $10$ terms will be:

> $1, 2, 3, 5, 8, 13, 21, 34, 55, 89, \dots$

By considering the terms in the Fibonacci sequence whose values do not exceed four million, find the sum of the even-valued terms.

### Answer

In [ ]:
sum(i for i in fibonacci_xrange(4*10^6) if i % 2 == 0)

4613732

If you did not discover the `fibonacci_xrange` function, or if it was not available (e.g. in another situation), you could have noticed that:

In [ ]:
fibonacci(50) > 4*10^6

True

So, since `fibonacci` is a non-decreasing sequence, you could have done:

In [ ]:
sum(fibonacci(n) for n in range(2*ceil(log(4*10^6,2))+1) if fibonacci(n) % 2 == 0 and fibonacci(n) <= 4*10^6)

4613732

This is not satisfactory, because if we replace four million by a lager number, the bound in the loop (here `50`), should be changed manually.

So, the main problem here is where to stop the `for` loop. A quick estimation shows that $\forall n\geq 5, \mbox{ fibonacci}(n) \geq 2^{n/2}$ (exercise: prove it !), hence we are sure that $\forall n \geq 2*\lceil 4*10^6 \rceil + 1, \mbox{
fibonacci}(n) \geq 4*10^6$. So, we can write the more generic:

In [ ]:
sum(fibonacci(n) for n in range(2*ceil(log(4*10^6,2))+1) if fibonacci(n) % 2 == 0 and fibonacci(n) <= 4*10^6)

4613732

Note that, if it was not possible to guess a lower bound on the Fibonacci sequence (hence the length of the loop), we could still use the fact that it is non-decreasing, hence once $\mbox{fibonacci}(n) > 4*10^6$, we know that no further values will be less than $4*10^6$. So, the following (non-one-liner) would be appropriate in such situations:

In [ ]:
s = 0
n = 0
while True:
    f = fibonacci(n)
    if f <= 4*10^6:
        if f % 2 == 0:
            s += f
    else:   
        break
    n += 1
s

4613732

## 3: Largest prime factor

### Question

The prime factors of $13195$ are $5$, $7$, $13$ and $29$.

What is the largest prime factor of the number $600851475143$ ?

### Answer

If tab-completion led you to the `factor` function, you can see that:

In [ ]:
list(factor(600851475143))

[(71, 1), (839, 1), (1471, 1), (6857, 1)]

gives you the list of `(prime factor, multiplicity)`, so you can extract the maximal prime factor as:

In [ ]:
max(f[0] for f in factor(600851475143))

6857

Note that the following also works:

In [ ]:
max(factor(600851475143))[0]

6857

Indeed, here the maximum is taken over the tuples, and then we extract the `0`-th element. This is still correct since the ordering on the tuples is the lexical one, so the largest tuple will be the tuple with largest `0`-th coordinate, this behaviour is guaranteed by [the Python documentation](https://docs.python.org/2/reference/expressions.html#not-in).

Of course, if you do not want to deal with multiplicities, you could search further and find the following:

In [ ]:
max(600851475143.prime_factors())

6857

or even:

In [ ]:
max(prime_divisors(600851475143))

6857

Note that the following is not valid:

In [ ]:
prime_divisors(600851475143)[-1]

6857

unless you get a *guarantee* that the `prime_divisors` function sorts the divisors in nondecreasing order. To be sure about this behaviour:

-   checking on some examples is not sufficient since you might miss some patterns that will behave differently.
-   looking at the source code might be an option, but you could not be sure that some developer change the behaviour to get an increase of speed in a further version. As long as a behaviour is not specified, the developpers have the right to change it.
-   the only reliable way is to ensure that the behaviour is explicitely specified, so you have to look at the documentation:

Fortunately, this is the case for this example:

In [ ]:
prime_divisors?

## 4: Largest palindrome product

### Question

A palindromic number reads the same both ways. The largest palindrome made from the product of two 2-digit numbers is

> $9009 = 91 \times 99$.

Find the largest palindrome made from the product of two 3-digit numbers.

### Answer

Looking at the Sage documentation (using e.g. the `search_doc` function), we see that there is a `Word` class that can decide whether a word is a palindrome, so we can do:

In [ ]:
max(i*j for i in range(100,1000) for j in range(100,1000) if Word(str(i*j)).is_palindrome())

906609

However, we see that it is pretty slow. This is because when Sage creates a word, it also has to create its parent, that is the set of words, and the way our loop is written, it will do it at each iteration. So, we can create the parent once for all as follows and then construct each word from this parent (though is it not strictly a one-liner anymore):

In [ ]:
W = Words('0123456789') ; max(i*j for i in range(100,1000) for j in range(100,1000) if W(str(i*j)).is_palindrome())

906609

It is much faster, but still quite slow. Since being a palindrome is not a complicated notion, we can just use strings and slices as follows:

In [ ]:
max(i*j for i in range(100,1000) for j in range(100,1000) if str(i*j) == str(i*j)[::-1])

906609

Which is much faster. Note however that for more involved computations, Sage words will propose features not available for strings (in a similar way that Sage `Integer` offers much more than Python `int`).

**Remark:** note the difference with:

In [ ]:
max([i*j for i in range(100,1000) for j in range(100,1000) if str(i*j) == str(i*j)[::-1]])

906609

This latter is slower since it first creates a list and then computes its maximum, while in the previous code, the maximum is computed on the fly from the iterator (no useless intermediary list is created).

## 5: Smallest multiple

### Question

$2520$ is the smallest number that can be divided by each of the numbers from $1$ to $10$ without any remainder.

What is the smallest positive number that is evenly divisible by all of the numbers from $1$ to $20$?

### Answer

In [ ]:
lcm(range(1,21))

232792560

Good to know some mathematical definitions !

## 6: Sum square difference

### Question

The sum of the squares of the first ten natural numbers is

> $1^2 + 2^2 + ... + 10^2 = 385$.

The square of the sum of the first ten natural numbers is

> $(1 + 2 + ... + 10)^2 = 552 = 3025$.

Hence the difference between the sum of the squares of the first ten natural numbers and the square of the sum is

> $3025 − 385 = 2640$.

Find the difference between the sum of the squares of the first one hundred natural numbers and the square of the sum.

### Answer

In [ ]:
sum(x for x in range(1,101))^2 - sum(x^2 for x in range(1,101))

25164150

Notice that for projecteuler, 0 is not a natural number, so the first ten natural numbers are $1, 2, ..., 10$ not $0, 1, ..., 9$. However, most mathematicians consider $0$ as a natural number.

Note that `(x for x in range(1,101))` is a stupid iterator that could be replaced by the faster `range(1,101)`.

Note also that, if the bound `100` had to be replaced by a much larger number, iterating over all numbers and summing them and their squares will be much slower than the following. Indeed, Sage symbolics is able to find a formula for both sums, which will be then evaluated in nearly constant time whatever the bound:

In [ ]:
(n,k) = SR.var('n,k')
expr = sum(k,k,1,n)^2 - sum(k^2,k,1,n) ; expr

-1/3*n^3 + 1/4*(n^2 + n)^2 - 1/2*n^2 - 1/6*n

In [ ]:
expr.subs(n=100)

25164150

In [ ]:
expr.subs(n=123^123)

4278138466403270721225008543350890417447832002411564036665278538164168893119381489263265771980780708001150090908937931159057716706929091973802366029482532161010037181170824846218403747354364843434060769720213794418167238841119162696488474149747409037354190149923587406936559794260692908806059759737479836740915957239183041691225308142184446975781065599760551593112386195142956618090375002657760984409353634294695536392085998982193137582840721946773913913359342900481262463391817360426347719449566845450957613529919809093064882655581756713526665679618950062677196159299654131583536989874159269635894596338706224455848351706716110782404343111525307151127820252911842097057740801301828669821084643098200243416788292390526975180955494485165261419244992865622904834270347067301861883710334131889442783819488756977837457520185671961324101832173416683971164447168761177527973078165140508264068154351292125946584725690050645277369252353771598452547850164595785211066680752884885930476720209441685508125821848

Could you imagine the previous loop running `123^123` times ? Symbolic computations are slow compared to their numerical equivalent, but they can save a lot of time by doing things numerics can't achieve !

## 7: 10001st prime

### Question

By listing the first six prime numbers: $2$, $3$, $5$, $7$, $11$, and $13$, we can see that the $6$-th prime is $13$.

What is the $10001$-st prime number?

### Answer

In [ ]:
nth_prime(10001)

104743

or,

In [ ]:
Primes().unrank(10000)

104743

Note that using the folloging method is a complete waste:

In [ ]:
primes_first_n(10001)[-1]

104743

Indeed, look at the source code of `primes_first_n` :

In [ ]:
primes_first_n??

As you can see, `primes_first_n` computes its last element with `nth_prime`, then it fills the list with smaller primes with `prime_range`, then we ask for the last element of that list !

## 8: Largest product in a series

### Question

The four adjacent digits in the 1000-digit number $n$ below that have the greatest product are

> $9 \times 9 \times 8 \times 9 = 5832$.

In [ ]:
n = 7316717653133062491922511967442657474235534919493496983520312774506326239578318016984801869478851843858615607891129494954595017379583319528532088055111254069874715852386305071569329096329522744304355766896648950445244523161731856403098711121722383113622298934233803081353362766142828064444866452387493035890729629049156044077239071381051585930796086670172427121883998797908792274921901699720888093776657273330010533678812202354218097512545405947522435258490771167055601360483958644670632441572215539753697817977846174064955149290862569321978468622482839722413756570560574902614079729686524145351004748216637048440319989000889524345065854122758866688116427171479924442928230863465674813919123162824586178664583591245665294765456828489128831426076900422421902267105562632111110937054421750694165896040807198403850962455444362981230987879927244284909188845801561660979191338754992005240636899125607176060588611646710940507754100225698315520005593572972571636269561882670428252483600823257530420752963450

Find the thirteen adjacent digits in the 1000-digit number that have the greatest product. What is the value of this product?

### Answer

In [ ]:
max(prod(ZZ(j) for j in str(n)[i:i+13]) for i in range(1000-12))

23514624000

To be sure about the endpoint, we can test with a number that ends with thirteen `9` :

In [ ]:
n_end = 7316717653133062491922511967442657474235534919493496983520312774506326239578318016984801869478851843858615607891129494954595017379583319528532088055111254069874715852386305071569329096329522744304355766896648950445244523161731856403098711121722383113622298934233803081353362766142828064444866452387493035890729629049156044077239071381051585930796086670172427121883998797908792274921901699720888093776657273330010533678812202354218097512545405947522435258490771167055601360483958644670632441572215539753697817977846174064955149290862569321978468622482839722413756570560574902614079729686524145351004748216637048440319989000889524345065854122758866688116427171479924442928230863465674813919123162824586178664583591245665294765456828489128831426076900422421902267105562632111110937054421750694165896040807198403850962455444362981230987879927244284909188845801561660979191338754992005240636899125607176060588611646710940507754100225698315520005593572972571636269561882670428252483600823257539999999999999

In [ ]:
max(prod(ZZ(j) for j in str(n_end)[i:i+13]) for i in range(1000-12)) == 9^13

True


In [ ]:
max(prod(ZZ(j) for j in str(n_end)[i:i+13]) for i in range(1000-13)) == 9^13

False

Note however that a slice in a string gives something consistent:

In [ ]:
'abcd'[2:10]

'cd'

In [ ]:
'abcd'[5:10]

''

Hence, we can go further and still get the correct answer without overflow:

In [ ]:
max(prod(ZZ(j) for j in str(n)[i:i+13]) for i in range(1000))

23514624000

## 9: Special Pythagorean triplet

### Question

A Pythagorean triplet is a set of three natural numbers, $a < b < c$, for which, $a^2 + b^2 = c^2$

For example, $3^2 + 4^2 = 9 + 16 = 25 = 5^2$.

There exists exactly one Pythagorean triplet for which $a + b + c = 1000$. Find the product $abc$.

### Answer

The worse answer we could imagine is the following (look at the timings):

In [ ]:
%time [prod([a,b,c]) for a in range(1,1000) for b in range(1,1000) for c in range(1,1000) if a^2+b^2==c^2 and a<b<c and a+b+c==1000][0]

CPU times: user 46min 21s, sys: 708 ms, total: 46min 22s
Wall time: 46min 28s
31875000

Indeed, we first test `a^2+b^2==c^2` (which requires non-trivial computation) before testing `a<b<c` or `a+b+c==1000` (which are faster to compute):

In [ ]:
%time [prod([a,b,c]) for a in range(1,1000) for b in range(1,1000) for c in range(1,1000) if a<b<c and a+b+c==1000 and a^2+b^2==c^2][0]

CPU times: user 6min 51s, sys: 52 ms, total: 6min 51s
Wall time: 6min 52s
31875000

We see that the order of tests has an importance in algorithmics: mathematically $A \mbox{ and } B$ is equivalent to $B \mbox{ and } A$, however, from a computational perspective, when we write `A and B`, `B` is not computed if `A` is `False`, so `A and B` is not equivalent to `B and A`. Similarly, in the computation of `A or B`, if `A` is `True`, then `B` is not evaluated.

Also, it is a big waste to loop over the whole product $\{1,\dots,1000\}^3$ and then check whether $a < b < c$ and $a + b + c = 1000$. First, $a$ do not need to take value larger than $333$, then $b$ do not need to take values smaller than $a$ nor larger than $499$ then $c$ is completely determined by the fact that $a+b+c=1000$, so it is useless to try all values between $0$ and $1000$ for $c$ while only one satisfies $a+b+c=1000$. We save a lot of useless iterations by doing:

In [ ]:
%time [prod([a,b,1000-a-b]) for a in range(1,334) for b in range(a+1,500) if a^2+b^2 == (1000-a-b)^2][0]

CPU times: user 908 ms, sys: 52 ms, total: 960 ms
Wall time: 749 ms
31875000

Note that one could be slightly more precise by saying that `b` can be not larger that $\lfloor(1000-a)/2\rfloor$ :

In [ ]:
%time [prod([a,b,1000-a-b]) for a in range(1,334) for b in range(a+1,floor((1000-a)/2)) if a^2+b^2 == (1000-a-b)^2][0]

CPU times: user 668 ms, sys: 60 ms, total: 728 ms
Wall time: 553 ms
31875000

However, note that we are already happy by the previous answer. It is also important to take the development time into account : if optimizing your code for 1 hour let you gain only a couple of hours of computation for a research code that will be run only once, then you lost your time. If your code will be run many times or by many people, then it might worth it.

## 10: Summation of primes

### Question

The sum of the primes below $10$ is $2 + 3 + 5 + 7 = 17$.

Find the sum of all the primes below two million.

### Answer

In [ ]:
sum(prime_range(2*10^6))

142913828922

If you did not discover the `prime_range` function, you could find the `is_prime` method by tab-completion from a Sage integer and do:

In [ ]:
sum(i for i in range(2*10^6) if ZZ(i).is_prime())

142913828922

or,

In [ ]:
sum(i for i in srange(2*10^6) if i.is_prime())

142913828922

## Some advices we learnt on the way

-   coding techniques
    -   Do not create lists if each entry is used once, use iterators instead (from question 4 and others).
    -   Do not re-create the same parent at each iteration (from question 4).
    -   Try to reduce the search space to be explored by loops (from quesion 9).
    -   Test the fastest-to-check condition first (from question 9).
-   code viability
    -   Do not assume behaviours that are not explicitely specified in the documentation (from question 3).
    -   Try to write generic code, in particular, do not hardcode ad-hoc constants so that you can reuse your code for a later use (from question 2).
    -   Take the development time into account.
    -   Verify corner cases with specific tests (from question 8).
-   improve your knowledge
    -   Knowing some mathematics might avoid lengthy computations, symbolic calculus could help here (from questions 5 and 6).
    -   Look at the source code to see if you are not missing something, and learn from developers (question 7).